In [1]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [2]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [3]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/FinancialProgressReport/finProgress_newRpt.aspx"
params = {
    'params': 0
}
for key, value in params.items():
    url = url #+ "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [4]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddl_finYear'
iay_radio_name = 'ctl00$ContentPlaceHolder1$rdlScheme'
excel_button = 'ctl00$ContentPlaceHolder1$btnExport'
content_table_class = 'table_s'

In [5]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

def check_table():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.CSS_SELECTOR, '.'+content_table_class))            
    WebDriverWait(driver, 2).until(element_present)
    
#Check Submit button
def delete_excel():
    driver.execute_script("return document.getElementsByName('" + excel_button + "')[0].remove()")
def check_excel():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, excel_button ) ) )

In [8]:
#Start Chrome
driver.get(url)
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[1:2]
print(yearlist)
for year in yearlist:
    print("--Scrapping data for Year: ", year['text'])
    #Start Chrome
    driver.get(url)
    #Year Selection
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(".//option[@value='0']").click()
    year_query = ".//option[@value='" + year['value'] + "']"
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    
    #DataStore
    df_list = []
    
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, iay_radio_name))
    )
    element.click()
    
    #state select
    check_table()
    temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[3:-2]
    states = []
    for row in temp_list:
        try:
            x = {}
            td = row.find_elements_by_xpath(".//td")[1]
            x['name'] = td.text
            x['link'] = td.find_element_by_tag_name("a").get_attribute("href")
            states.append(x)
        except Exception as e:
            print("Error while parsing table data |", e)
    for state in states:
        print("----Scrapping data for State: ", state['name'])
        driver.get(state['link'])
        check_table()
        temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
        districts = []
        for row in temp_list:
            x = {}            
            x['name'] = row.find_elements_by_xpath(".//td")[1].text
            x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
            districts.append(x)
        for district in districts:
            print("------Scrapping data for District: ", district['name'])
            driver.get(district['link'])
            check_table()
            temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
            blocks = []
            for row in temp_list:
                x = {}            
                x['name'] = row.find_elements_by_xpath(".//td")[1].text
                x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                blocks.append(x)
            
            for block in blocks:
                print("--------Scrapping data for Block: ", block['name'])
                driver.get(block['link'])
                try:
                    check_table()
                    html_table = driver.find_element_by_class_name(content_table_class).get_attribute('outerHTML')
                    df = pd.read_html(html_table, header=3)[0]
                    df = df[:-1]
                    #df.columns = table_head
                    df['Financial Year'] = year['text']
                    df['State Name'] = state['name']
                    df['District Name'] = district['name']
                    df['Block Name'] = block['name']
                    df_list.append(df)
                except Exception as e:
                    print("Error while table data |", e)
                
    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df.drop(df.columns[0],axis=1,inplace=True)
    df = df.reset_index()
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

[{'text': '2011-2012', 'value': '2011-2012 '}]
--Scrapping data for Year:  2011-2012
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=66.0.3359.181)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
----Scrapping data for State:  ASSAM
------Scrapping data for District:  BARPETA
--------Scrapping data for Block:  RUPSHI
------Scrapping data for District:  CACHAR
--------Scrapping data for Block:  SONAI
--------Scrapping data for Block:  UDHARBOND
------Scrapping data for District:  DHEMAJI
--------Scrapping data for Block:  DHEMAJI
--------Scrapping data for Block:  MURKONGSELEK
------Scrapping data for District:  DIBRUGARH
--------Scrapping data for Block:  BORBORUAH
------Scrapping data for District:  KAMRUP
--------Scrapping data for Block:  BIHDIA JAJIKONA
--------S

------Scrapping data for District:  GOPALGANJ
--------Scrapping data for Block:  BAIKUNTHPUR
--------Scrapping data for Block:  BARAULI
--------Scrapping data for Block:  BHOREY
--------Scrapping data for Block:  BIJAIPUR
--------Scrapping data for Block:  GOPALGANJ
--------Scrapping data for Block:  HATHUA
--------Scrapping data for Block:  KATAIYA
--------Scrapping data for Block:  KUCHAIKOTE
--------Scrapping data for Block:  MANJHA
--------Scrapping data for Block:  PANCHDEORI
--------Scrapping data for Block:  PHULWARIYA
--------Scrapping data for Block:  SIDHWALIA
--------Scrapping data for Block:  THAWE
--------Scrapping data for Block:  UCHKAGAON
------Scrapping data for District:  JAMUI
--------Scrapping data for Block:  BARHAT
--------Scrapping data for Block:  CHAKAI
--------Scrapping data for Block:  GIDHOR
--------Scrapping data for Block:  ISLAMNAGAR ALIGANJ
--------Scrapping data for Block:  JAMUI
--------Scrapping data for Block:  JHAJHA
--------Scrapping data for Block

------Scrapping data for District:  PASHCHIM CHAMPARAN
--------Scrapping data for Block:  BAGAHA-I
--------Scrapping data for Block:  BAGAHA-II
--------Scrapping data for Block:  BAIRIA
--------Scrapping data for Block:  BETTIAH
--------Scrapping data for Block:  BHITAHA
--------Scrapping data for Block:  CHANPATIA
--------Scrapping data for Block:  GAUNAHA
--------Scrapping data for Block:  JOGAPATTI
--------Scrapping data for Block:  LAURIYA
--------Scrapping data for Block:  MADHUBANI
--------Scrapping data for Block:  MAINATAND
--------Scrapping data for Block:  MAJHAULIA
--------Scrapping data for Block:  NARKATIAGANJ
--------Scrapping data for Block:  NAUTAN
--------Scrapping data for Block:  PIPRASI
--------Scrapping data for Block:  RAMNAGAR
--------Scrapping data for Block:  SIKTA
--------Scrapping data for Block:  THAKRAHAN
------Scrapping data for District:  PATNA
--------Scrapping data for Block:  ATHMALGOLA
--------Scrapping data for Block:  BAKHTIYARPUR
--------Scrapping 

--------Scrapping data for Block:  RUNNISAIDPUR
--------Scrapping data for Block:  SONBARSA
--------Scrapping data for Block:  Suppi
--------Scrapping data for Block:  SURSAND
------Scrapping data for District:  SIWAN
--------Scrapping data for Block:  ANDAR
--------Scrapping data for Block:  BARHARIA
--------Scrapping data for Block:  BASANTPUR
--------Scrapping data for Block:  BHAGWANPUR HAT
--------Scrapping data for Block:  DARAULI
--------Scrapping data for Block:  DARAUNDHA
--------Scrapping data for Block:  GORIAKOTHI
--------Scrapping data for Block:  GUTHANI
--------Scrapping data for Block:  HASANPUR
--------Scrapping data for Block:  HUSSAINGANJ
--------Scrapping data for Block:  JIRADEI
--------Scrapping data for Block:  LAKRI NABIGANJ
--------Scrapping data for Block:  MAHARAJGANJ
--------Scrapping data for Block:  MAIRWA
--------Scrapping data for Block:  NAUTAN
--------Scrapping data for Block:  PACHRUKHI
--------Scrapping data for Block:  RAGHUNATHPUR
--------Scrapping

--------Scrapping data for Block:  PALSANA
--------Scrapping data for Block:  UMARPADA
------Scrapping data for District:  VADODARA
--------Scrapping data for Block:  CHHOTA UDAIPUR
--------Scrapping data for Block:  DABHOI
--------Scrapping data for Block:  DESAR
--------Scrapping data for Block:  JETPUR PAVI
--------Scrapping data for Block:  KAWANT
--------Scrapping data for Block:  NASVADI
--------Scrapping data for Block:  SAVLI
------Scrapping data for District:  VALSAD
--------Scrapping data for Block:  DHARAMPUR
--------Scrapping data for Block:  KAPRADA
--------Scrapping data for Block:  VALSAD
----Scrapping data for State:  HARYANA
------Scrapping data for District:  AMBALA
--------Scrapping data for Block:  AMBALA-I
------Scrapping data for District:  BHIWANI
--------Scrapping data for Block:  LOHARU
------Scrapping data for District:  FARIDABAD
--------Scrapping data for Block:  BALLABGARH
--------Scrapping data for Block:  FARIDABAD
------Scrapping data for District:  FATE

...

--------Scrapping data for Block:  द‍ौसा
--------Scrapping data for Block:  बांदीकुई
--------Scrapping data for Block:  महवा
--------Scrapping data for Block:  लालसोट
--------Scrapping data for Block:  सिकराय
------Scrapping data for District:  DHOLPUR
--------Scrapping data for Block:  ध‍ौलपुर
--------Scrapping data for Block:  बसेडी
--------Scrapping data for Block:  बाडी
--------Scrapping data for Block:  राजाखेडा
------Scrapping data for District:  DUNGARPUR
--------Scrapping data for Block:  आसपुर
--------Scrapping data for Block:  डूंगरपुर
--------Scrapping data for Block:  बिछीवाडा
--------Scrapping data for Block:  सागवाडा
--------Scrapping data for Block:  सीमलवाडा
------Scrapping data for District:  HANUMANGARH
--------Scrapping data for Block:  Bhadra
--------Scrapping data for Block:  Hanumangarh
--------Scrapping data for Block:  Nohar
--------Scrapping data for Block:  PILIBANGAN
--------Scrapping data for Block:  RAWATSAR
--------Scrapping data for Block:  SANGRIA
------

----Scrapping data for State:  UTTAR PRADESH
------Scrapping data for District:  AGRA
--------Scrapping data for Block:  ACHHNERA
--------Scrapping data for Block:  AKOLA
--------Scrapping data for Block:  BAH
--------Scrapping data for Block:  BARAULI AHIR
--------Scrapping data for Block:  BICHPURI
--------Scrapping data for Block:  ETMADPUR
--------Scrapping data for Block:  FATEHABAD
--------Scrapping data for Block:  FATEHPUR SIKRI
--------Scrapping data for Block:  JAGNER
--------Scrapping data for Block:  JAITPUR KALAN
--------Scrapping data for Block:  KHANDAULI
--------Scrapping data for Block:  KHERAGARH
--------Scrapping data for Block:  PINAHAT
--------Scrapping data for Block:  SAIYAN
--------Scrapping data for Block:  SHAMSABAD
------Scrapping data for District:  ALLAHABAD
--------Scrapping data for Block:  BAHADURPUR
--------Scrapping data for Block:  CHAKA
------Scrapping data for District:  AMBEDKAR NAGAR
--------Scrapping data for Block:  Akbarpur
--------Scrapping da

--------Scrapping data for Block:  ZAMANIA
------Scrapping data for District:  GONDA
--------Scrapping data for Block:  BELSAR
--------Scrapping data for Block:  CHHAPIA
--------Scrapping data for Block:  COLONELGANJ
--------Scrapping data for Block:  HALDHARMAU
--------Scrapping data for Block:  ITIATHOK
--------Scrapping data for Block:  JHANJHARI
--------Scrapping data for Block:  NAWABGANJ
--------Scrapping data for Block:  PANDRI KRIPAL
--------Scrapping data for Block:  PARASPUR
--------Scrapping data for Block:  RUPAIDEEH
--------Scrapping data for Block:  TARABGANJ
--------Scrapping data for Block:  WAZIRGANJ
------Scrapping data for District:  GORAKHPUR
--------Scrapping data for Block:  BELGHAT
--------Scrapping data for Block:  BHATHAT
--------Scrapping data for Block:  GAUGAHA
--------Scrapping data for Block:  KAURI RAM
------Scrapping data for District:  HAMIRPUR
--------Scrapping data for Block:  MUSKARA
------Scrapping data for District:  HARDOI
--------Scrapping data f

--------Scrapping data for Block:  MANDHATA
--------Scrapping data for Block:  PATTI
--------Scrapping data for Block:  PRATAPGARH (SADAR)
--------Scrapping data for Block:  RAMPUR SANRAMGARH
--------Scrapping data for Block:  SANDWA CHANDRIKA
--------Scrapping data for Block:  SANGIPUR
--------Scrapping data for Block:  SHIVGARH
------Scrapping data for District:  RAE BARELI
--------Scrapping data for Block:  AMAWAN
--------Scrapping data for Block:  BACHHRAWAN
--------Scrapping data for Block:  CHHATOH
--------Scrapping data for Block:  DALMAU
--------Scrapping data for Block:  DEENSHAH GAURA
--------Scrapping data for Block:  DIH
--------Scrapping data for Block:  HARCHANDPUR
--------Scrapping data for Block:  JAGATPUR
--------Scrapping data for Block:  KHIRON
--------Scrapping data for Block:  LALGANJ
--------Scrapping data for Block:  RAHI
--------Scrapping data for Block:  ROHANIA
--------Scrapping data for Block:  SALON
--------Scrapping data for Block:  SARENI
--------Scrapping

--------Scrapping data for Block:  GAZOLE
------Scrapping data for District:  NADIA
--------Scrapping data for Block:  CHAPRA
--------Scrapping data for Block:  HANSKHALI
------Scrapping data for District:  PASCHIM MEDINIPUR
--------Scrapping data for Block:  MIDNAPORE
------Scrapping data for District:  PURBA MEDINIPUR
--------Scrapping data for Block:  BHAGWANPUR-II
--------Scrapping data for Block:  CONTAI-III
--------Scrapping data for Block:  KHEJURI-II
--------Scrapping data for Block:  MOYNA
--------Scrapping data for Block:  NANDIGRAM-II
--------Scrapping data for Block:  PANSKURA-I
--------Scrapping data for Block:  RAMNAGAR-I
--------Scrapping data for Block:  SHAHID MATANGINI
----Scrapping data for State:  ANDAMAN AND NICOBAR
------Scrapping data for District:  NORTH AND MIDDLE ANDAMAN
--------Scrapping data for Block:  MAYABUNDER
----Scrapping data for State:  DADRA AND NAGAR HAVELI
----Scrapping data for State:  DAMAN AND DIU
----Scrapping data for State:  LAKSHADWEEP
----